##### PROJETO INTEGRADOR  |  PREVISÃO DE DEMANDA  |   VENDAS AUTOPEÇAS (GRUPO 100 VIES)


# IMPORTANDO BIBLIOTECAS

In [117]:
#IMPORTANDO BIBLIOTECAS
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

import matplotlib.pyplot as plt
from sklearn import metrics
from sklearn.model_selection import train_test_split
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import plotly
import os
from imblearn.over_sampling import SMOTE
import janitor

pd.set_option('display.max_rows', None)
params = {'legend.fontsize': 'x-large',
          'figure.figsize': (16, 8),
          'axes.labelsize': 'x-large',
          'axes.titlesize':'x-large',
          'xtick.labelsize':'x-large',
          'ytick.labelsize':'x-large'}

%matplotlib inline
plt.rcParams.update(params)

In [118]:
import plotly_express as px

# IMPORTANDO O .CSV DE VENDAS

In [119]:
vendas=pd.read_csv("1-Vendas_Integrador_100Vies-Rev1.csv",sep=',',encoding='Latin1')
vendas.head()

Codigo                                 Descricao  NotaFiscal   DataVenda  \
0  3570301              SEMI EIXO 41 ESTRIAS 8 FUROS       14424  29/10/2018   
1      782  LANTERNA TRASEIRA 155MM LED VERMELHA 24V       13934  01/08/2018   
2      782  LANTERNA TRASEIRA 155MM LED VERMELHA 24V       14612  03/12/2018   
3      782  LANTERNA TRASEIRA 155MM LED VERMELHA 24V       15779  02/05/2019   
4     1718            LANTERNA TRASEIRA  AMARELA 24V       14108  03/09/2018   

   Quantidade  LinhaProduto  ClienteGrupo  Cliente  CentroCusto  \
0           1           999          1047       49        21410   
1           1            14          1047      258        21410   
2           1            14          1047      258        21410   
3           1            14          1047      258        21410   
4           2            14          1047      258        21410   

   EstoqueMinimo DataUltimaCompra DataUltimaVenda  
0              0       10/10/2018      29/10/2018  
1              0       22/11/2018      02/05/2019  
2              0       22/11/2018      02/05/2019  
3              0       22/11/2018      02/05/2019  
4              0       22/11/2018      03/04/2019

# EXPLORAÇÃO DOS DADOS 

In [120]:
vendas.LinhaProduto.value_counts()

2      18793
1      17928
7       8583
10      5597
999     4637
8       3783
9       3496
11      3486
14      1898
3       1169
13      1122
102     1077
107      385
12       383
6        368
101      243
5        227
Name: LinhaProduto, dtype: int64

In [121]:
vendas['DataVenda'] = pd.to_datetime(vendas['DataVenda'],dayfirst=True)

In [122]:
vendas.DataVenda.head()

0   2018-10-29
1   2018-08-01
2   2018-12-03
3   2019-05-02
4   2018-09-03
Name: DataVenda, dtype: datetime64[ns]

In [123]:
vendas.LinhaProduto.value_counts()

2      18793
1      17928
7       8583
10      5597
999     4637
8       3783
9       3496
11      3486
14      1898
3       1169
13      1122
102     1077
107      385
12       383
6        368
101      243
5        227
Name: LinhaProduto, dtype: int64

# SELECIONANDO SOMENTE VENDAS DE PRODUTOS MERCEDES  (Linhas 1 e 2 )

In [124]:
# vendasmbb: somente vendas de peças das linhas 1 e 2 da Mercedes, porém com todos os Centros de Custo
vendasmbb = vendas[vendas['LinhaProduto'] <= 2]
vendasmbb.head()

Codigo                        Descricao  NotaFiscal  \
1066          A0000100105   JG.DE JUNTAS DO BLOCO DE MOTOR       13538   
1067          A0000100105   JG.DE JUNTAS DO BLOCO DE MOTOR       14294   
1068          A0000100105   JG.DE JUNTAS DO BLOCO DE MOTOR       17894   
1072  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12750   
1073  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12759   

      DataVenda  Quantidade  LinhaProduto  ClienteGrupo  Cliente  CentroCusto  \
1066 2018-05-08           1             2          1223      256        21410   
1067 2018-10-08           1             2          1223      256        21410   
1068 2020-01-10           1             2          1223      256        21410   
1072 2017-08-30           6             1          1045       47        21320   
1073 2017-09-04           6             1          1045       46        21320   

      EstoqueMinimo DataUltimaCompra DataUltimaVenda  
1066              0       13/12/2019      10/01/2020  
1067              0       13/12/2019      10/01/2020  
1068              0       13/12/2019      10/01/2020  
1072              0       12/12/2018      10/01/2020  
1073              0       12/12/2018      10/01/2020

In [125]:
#Linha1: Caminhoes e Onibus MBB
#Linha2: Vans MBB
vendasmbb.LinhaProduto.value_counts()

2    18793
1    17928
Name: LinhaProduto, dtype: int64

In [126]:
#CC 21410: Oficina
#CC 21320: Telepeças
vendasmbb.CentroCusto.value_counts()

21410    21806
21320     9646
21330     2779
22330     2075
20380      253
22410       94
21310       43
28880       22
20350        2
21350        1
Name: CentroCusto, dtype: int64

# SELECIONANDO SOMENTE VENDAS PELO CANAL TELEPEÇAS (C.C. 21320)

In [127]:
#vendastelep: linhas 1 e 2 MBB apenas com Centro de Custo Telepecas
vendastelep = vendasmbb[vendasmbb['CentroCusto'] == 21320]
vendastelep.CentroCusto.value_counts()

21320    9646
Name: CentroCusto, dtype: int64

In [128]:
vendastelep = vendastelep.drop(['CentroCusto'],axis=1)
vendastelep.head()

Codigo                        Descricao  NotaFiscal  \
1072  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12750   
1073  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12759   
1074  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       13246   
1075  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       13677   
1076  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       16871   

      DataVenda  Quantidade  LinhaProduto  ClienteGrupo  Cliente  \
1072 2017-08-30           6             1          1045       47   
1073 2017-09-04           6             1          1045       46   
1074 2018-02-22           2             1          1037       38   
1075 2018-06-08           2             1          1037       38   
1076 2019-09-05           2             1          1116      138   

      EstoqueMinimo DataUltimaCompra DataUltimaVenda  
1072              0       12/12/2018      10/01/2020  
1073              0       12/12/2018      10/01/2020  
1074              0       12/12/2018      10/01/2020  
1075              0       12/12/2018      10/01/2020  
1076              0       12/12/2018      10/01/2020

In [129]:
vendastelep.head()

Codigo                        Descricao  NotaFiscal  \
1072  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12750   
1073  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       12759   
1074  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       13246   
1075  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       13677   
1076  A00001003010064      TAMPA DO BOCAL DE ABASTECIMENTO       16871   

      DataVenda  Quantidade  LinhaProduto  ClienteGrupo  Cliente  \
1072 2017-08-30           6             1          1045       47   
1073 2017-09-04           6             1          1045       46   
1074 2018-02-22           2             1          1037       38   
1075 2018-06-08           2             1          1037       38   
1076 2019-09-05           2             1          1116      138   

      EstoqueMinimo DataUltimaCompra DataUltimaVenda  
1072              0       12/12/2018      10/01/2020  
1073              0       12/12/2018      10/01/2020  
1074              0       12/12/2018      10/01/2020  
1075              0       12/12/2018      10/01/2020  
1076              0       12/12/2018      10/01/2020

In [130]:
vendastelep.LinhaProduto.value_counts()

1    8083
2    1563
Name: LinhaProduto, dtype: int64

# ORDENANDO O DATASET PELA DATA DE VENDA

In [131]:
vendastelep = vendastelep.sort_values(by=['DataVenda'])

In [132]:
vendastelep.reset_index()

index               Codigo  \
0     42137          A9017601347   
1     45587          A9064230312   
2     50313          A9702540508   
3     37331          A6968300042   
4     35633          A6886717310   
5     36772          A6934900319   
6     29888          A6120103320   
7     36764          A6934607105   
8     26479          A4479060800   
9     13231          A0149971792   
10    30957          A6462000570   
11    32991          A6510960380   
12    60145        N910142006001   
13    28945          A6110900350   
14    32947          A6510960280   
15    33904          A6511800722   
16    34457          A6512002301   
17    34633          A6512010180   
18     7835          A0018262782   
19     6539  A0009913940    9051   
20    28786          A6110707632   
21    52587          A9795280082   
22     2315          A0002006823   
23    28745          A6110702932   
24    29893          A6120703832   
25    28693          A6110702032   
26    10103          A0051531328   
27    52566          A9794900065   
28    37062          A6944200726   
29    36768          A6934900110   
30    36796  A6936660009    9004   
31    36775          A6934900601   
32    36794  A6936287007    0000   
33    37081          A6948107037   
34    37076          A6947607161   
35     7903          A0019873140   
36    49002          A9069933996   
37    35634          A6886717310   
38    26480          A4479060800   
39    33905          A6511800722   
40    33081          A6510960540   
41    44057          A9061420280   
42     7430          A0015450709   
43    32008          A6510520100   
44    31518          A6510500016   
45    31916          A6510520000   
46     4866          A0008201277   
47    43738          A9060180082   
48    35390          A6824210074   
49    37066          A6946800187   
50    36797          A6938100018   
51    36765          A6934607105   
52     8893          A0034310212   
53    28582          A6110520416   
54     9139          A0039977594   
55     8191          A0024667501   
56    28549          A6110520016   
57    28571          A6110520316   
58    29590          A6111870580   
59    14428          A0249972747   
60    26440          A4429915022   
61     3041          A0004308026   
62    37105          A6948307005   
63    35635          A6886717310   
64    23208          A3453307335   
65    23209          A3453307435   
66     3148          A0004600583   
67     3147          A0004600043   
68     4791          A0008111122   
69    34377          A6512001870   
70     3003          A0004203682   
71    23045          A3318697058   
72    45494          A9064200320   
73    37102          A6948207253   
74    37103          A6948257151   
75    37080          A6948107030   
76    37077          A6947607161   
77    47023      A90663778197000   
78    47578          A9068200261   
79    48435  A9068821014    9B51   
80    47472          A9068110107   
81    48169  A9068604285    9A86   
82    10782          A0069937901   
83    34380          A6512001870   
84    22254          A2038700951   
85    27824          A6013210350   
86    45109          A9063262181   
87     7165          A0012628102   
88     7164          A0012623323   
89    34027          A6512000270   
90    46550          A9065401517   
91    30506          A6395401517   
92     9559          A0044206920   
93    10585          A0064208420   
94    37287          A6955457045   
95    36773          A6934900319   
96    35396          A6829807164   
97    29931          A6209970490   
98    46551          A9065401517   
99     8804          A0029979790   
100   32426          A6510902952   
101   33660          A6511800109   
102   31372          A6510305105   
103   47859          A9068300218   
104   31373          A6510305105   
105   47579          A9068200261   
106   48369  A9068804170    9B51   
107   14190          A0209970448   
108   14268          A0232500201   
109   17044          A1179970230   
110   4219

In [133]:
vendastelep.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9646 entries, 42137 to 35263
Data columns (total 11 columns):
Codigo              9646 non-null object
Descricao           9646 non-null object
NotaFiscal          9646 non-null int64
DataVenda           9646 non-null datetime64[ns]
Quantidade          9646 non-null int64
LinhaProduto        9646 non-null int64
ClienteGrupo        9646 non-null int64
Cliente             9646 non-null int64
EstoqueMinimo       9646 non-null int64
DataUltimaCompra    9646 non-null object
DataUltimaVenda     9646 non-null object
dtypes: datetime64[ns](1), int64(6), object(4)
memory usage: 904.3+ KB


# CRIANDO FEATURES DATE TIME

In [134]:
vendastelep['YearVenda'] = vendastelep['DataVenda'].dt.year
vendastelep['YearMonth'] = vendastelep['DataVenda'].dt.to_period('M')
vendastelep['YearWeek'] = vendastelep.DataVenda.dt.strftime('%Y-w%U')
vendastelep['WeekVenda'] = vendastelep['DataVenda'].dt.week
vendastelep['WeekDay'] = vendastelep['DataVenda'].dt.weekday

In [135]:
vendastelep.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9646 entries, 42137 to 35263
Data columns (total 16 columns):
Codigo              9646 non-null object
Descricao           9646 non-null object
NotaFiscal          9646 non-null int64
DataVenda           9646 non-null datetime64[ns]
Quantidade          9646 non-null int64
LinhaProduto        9646 non-null int64
ClienteGrupo        9646 non-null int64
Cliente             9646 non-null int64
EstoqueMinimo       9646 non-null int64
DataUltimaCompra    9646 non-null object
DataUltimaVenda     9646 non-null object
YearVenda           9646 non-null int64
YearMonth           9646 non-null period[M]
YearWeek            9646 non-null object
WeekVenda           9646 non-null int64
WeekDay             9646 non-null int64
dtypes: datetime64[ns](1), int64(9), object(5), period[M](1)
memory usage: 1.3+ MB


# AGRUPANDO AS VENDAS POR: ANO, MÊS, SEMANA, DATA, DIA DA SEMANA

In [136]:
vendasporano = vendastelep.groupby(['YearVenda'])['Codigo'].count()
vendaspormes = vendastelep.groupby(['YearMonth'])['Codigo'].count()
vendasporsemana = vendastelep.groupby(['YearWeek'])['Codigo'].count()
vendaspordata = vendastelep.groupby(['DataVenda'])['Codigo'].count()
vendasweekday = vendastelep.groupby(['WeekDay'])['Codigo'].count()

In [137]:
vendasporano = pd.DataFrame(vendasporano)
vendaspormes = pd.DataFrame(vendaspormes)
vendasporsemana = pd.DataFrame(vendasporsemana)
vendaspordata = pd.DataFrame(vendaspordata)
vendasweekday = pd.DataFrame(vendasweekday)



In [138]:
vendasporano.reset_index()
vendaspormes.reset_index()
vendasporsemana.reset_index()
vendaspordata.reset_index()
vendasweekday.reset_index().head()

WeekDay  Codigo
0        0    1606
1        1    2160
2        2    2000
3        3    1971
4        4    1909

In [139]:
vendasporano['YearVenda'] = vendasporano.index
vendaspormes['YearMonth'] = vendaspormes.index
vendasporsemana['YearWeek'] = vendasporsemana.index
vendaspordata['DataVenda'] = vendaspordata.index
vendasweekday['WeekDay'] = vendasweekday.index

In [140]:
vendasporano['YearVenda']=vendasporano['YearVenda'].astype(str)
vendaspormes['YearMonth']=vendaspormes['YearMonth'].astype(str)
vendasporsemana['YearWeek']=vendasporsemana['YearWeek'].astype(str)
vendaspordata['DataVenda']=vendaspordata['DataVenda'].astype(str)
vendasweekday['WeekDay']=vendasweekday['WeekDay'].astype(str)

# GRÁFICOS DAS SÉRIES DE VENDAS

In [141]:
import plotly.express as px
fig = px.bar(vendasweekday, x="WeekDay", y="Codigo", text="Codigo",title="Qtd.de Vendas/Dia da Semana")
fig.show()

In [142]:
import plotly.express as px
fig = px.bar(vendasporano, x="YearVenda", y="Codigo", text="Codigo",title="Qtd.de Vendas/Ano")
fig.show()

In [143]:
import plotly.express as px
fig = px.bar(vendaspormes, x="YearMonth", y="Codigo", text="Codigo",title="Qtd.de Vendas/Mês")
fig.show()

In [144]:
import plotly.express as px
fig = px.line(vendasporsemana, x="YearWeek", y="Codigo",title="Qtd.de Vendas/Semana")
fig.show()

In [145]:
import plotly.express as px
fig = px.line(vendaspordata, x="DataVenda", y="Codigo",title="Qtd.de Vendas/Data")
fig.show()